Score passages using a simple neural network.

In [2]:
import json
from sklearn.svm import SVC

In [94]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import random_split

In [3]:
path_train = 'scores/dev.jl'

In [143]:
def read_rows(path):
    rows = []
    for line in open(path):
        rows.append(json.loads(line))
    return rows

def write_json_format(path_out, rows):
    f_out = open(path_out, 'w')
    for row in rows:
        f_out.write(json.dumps(row, ensure_ascii=False)+'\n')

rows = read_rows(path_train)

In [144]:
rows_train, rows_dev = random_split(rows, [0.9, 0.1])

In [145]:
X_train = torch.tensor([[
    row['score_bm25'], 
    row['score_bm25_not_lemmatized'], 
    row['score_bm25_bigrams'], 
    row['score_miniLM'],
    row['score_miniLM_combined'],
    row['score_miniLM_answers'],
] for row in rows_train])
X_dev = torch.tensor([[
    row['score_bm25'], 
    row['score_bm25_not_lemmatized'], 
    row['score_bm25_bigrams'], 
    row['score_miniLM'],
    row['score_miniLM_combined'],
    row['score_miniLM_answers'],
] for row in rows_dev])
y_train = torch.tensor([[float(row['label'])] for row in rows_train])
y_dev = torch.tensor([[float(row['label'])] for row in rows_dev])

In [146]:
in_features = len(X_train[0])
hid_features = 20
out_features = 1

model = nn.Sequential(
    nn.Linear(in_features, hid_features),
    nn.ReLU(),
    nn.Linear(hid_features, out_features),
    nn.Sigmoid()
)

In [147]:
model

Sequential(
  (0): Linear(in_features=6, out_features=20, bias=True)
  (1): ReLU()
  (2): Linear(in_features=20, out_features=1, bias=True)
  (3): Sigmoid()
)

In [148]:
def test_loss(model, X_test, y_test):
    outputs = model(X_test)
    return loss_fn(outputs, y_test)

In [149]:
test_loss(model, X_dev, y_dev)

tensor(0.1470, grad_fn=<BinaryCrossEntropyBackward0>)

In [150]:
loss_fn = nn.BCELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.01)

In [151]:
batch_size = 16
losses = []
num_epochs = 1
for epoch in range(num_epochs):
    for i in range(0, len(X_train), batch_size):
        inputs = X_train[i:i+batch_size]
        labels = y_train[i:i+batch_size]
        optimizer.zero_grad()
        
        outputs = model(inputs)
        loss = loss_fn(outputs, labels)
        loss.backward()
        
        optimizer.step()

        losses.append(loss)

In [152]:
test_loss(model, X_dev, y_dev)

tensor(0.0556, grad_fn=<BinaryCrossEntropyBackward0>)

In [174]:
path_test = 'scores/test-legal.jl'
rows_test = read_rows(path_test)

In [175]:
X_test = torch.tensor([[
    row['score_bm25'], 
    row['score_bm25_not_lemmatized'], 
    row['score_bm25_bigrams'], 
    row['score_miniLM'],
    row['score_miniLM_combined'],
    row['score_miniLM_answers'],
] for row in rows_test])

In [176]:
model(X_test)

tensor([[1.4472e-01],
        [1.4472e-01],
        [5.8871e-02],
        ...,
        [3.6163e-05],
        [6.4673e-06],
        [6.3025e-06]], grad_fn=<SigmoidBackward0>)

In [177]:
outputs = model(X_test)

In [178]:
for row, output in zip(rows_test, outputs):
    row['nn_score'] = float(output)

In [179]:
rows_test

[{'question_id': 0,
  'question_text': 'Ile trwa kadencja szefa służby cywilnej?',
  'passage_id': '1999_483_9',
  'passage_text': 'Art. 9. 1. Szefa Służby Cywilnej powołuje, po zasięgnięciu opinii Rady Służby Cywilnej, Prezes Rady Ministrów spośród urzędników służby cywilnej. 2. Kadencja Szefa Służby Cywilnej trwa 5 lat, licząc od dnia powołania; Szef Służby Cywilnej pełni obowiązki do dnia powołania jego następcy. 3. Kadencja Szefa Służby Cywilnej wygasa w razie jego śmierci lub odwołania. 4. Prezes Rady Ministrów odwołuje Szefa Służby Cywilnej w razie: 1) rezygnacji ze stanowiska, 2) utraty zdolności do pełnienia powierzonych obowiązków na skutek długotrwałej choroby, trwającej co najmniej 6 miesięcy. 5. Prezes Rady Ministrów odwołuje Szefa Służby Cywilnej także w przypadku, gdy przestał on odpowiadać jednemu z warunków określonych w art. 4. Odwołanie w przypadkach, o których mowa w art. 4 pkt 4 i 5, następuje za zgodą co najmniej 23 składu Rady Służby Cywilnej.',
  'score_bm25': 30

In [180]:
write_json_format(path_test, rows_test)